In [1]:
import pandas as pd
import numpy as np
import yfinance as yf
import arch
from arch.unitroot import ADF
from arch import arch_model
import matplotlib.pyplot as plt
import datetime

In [2]:
def full_month(ticker):
    today = datetime.datetime.now()
    four = (today - datetime.timedelta(days = 28)).date().strftime("%Y-%m-%d")
    three = (today - datetime.timedelta(days = 21)).date().strftime("%Y-%m-%d")
    two = (today - datetime.timedelta(days = 14)).date().strftime("%Y-%m-%d")
    one = (today - datetime.timedelta(days = 7)).date().strftime("%Y-%m-%d")
    t43 = yf.download(tickers=ticker, start=four, end=three, interval="1m")
    t32 = yf.download(tickers=ticker, start=three, end=two, interval="1m")
    t21 = yf.download(tickers=ticker, start=two, end=one, interval="1m")
    t10 = yf.download(tickers=ticker, period="7d", interval="1m")
    ticker = pd.concat([t43, t32, t21, t10])
    return ticker

In [3]:
def conditional_vol(ticker):
    ticker = full_month(ticker)
    returns = 10000 * (ticker["Close"].pct_change().dropna())
    arch = arch_model(returns, dist="skewt")
    result = arch.fit()
    return ticker, returns, result.conditional_volatility

In [4]:
def get_hurst_exponent(data):
    time_series = data["Close"].values
    lags = range(2, 12)
    tau = [np.std(np.subtract(time_series[lag:], time_series[:-lag])) for lag in lags]
    reg = np.polyfit(np.log(lags), np.log(tau), 1)
    return reg[0]

In [5]:
def t1_to_t2_dynamic(ticker1, ticker2, correlated, std_ct):
    t1, t1_returns, t1_vol = conditional_vol(ticker1)
    t2, t2_returns, t2_vol = conditional_vol(ticker2)
    hurst = get_hurst_exponent(t2)
    if correlated:
        t1_diff = t1_returns - t1_vol
        t1_times = t1_diff[t1_diff > 0].reset_index()
    else:
        t1_diff = t1_returns + t1_vol
        t1_times = t1_diff[t1_diff < 0].reset_index()
    t2 = t2.reset_index().reset_index()
    t2_vol = t2_vol.reset_index()
    entries = t2.loc[t2["Datetime"].isin(t1_times["Datetime"])].reset_index(drop=True)
    entry_vols = t2_vol.loc[t2_vol["Datetime"].isin(t1_times["Datetime"])].reset_index(drop=True)
    entries["Current Vol"] = entry_vols["cond_vol"]
    ctime = entries["Datetime"][0]
    profit = 0
    for index, row in entries.iterrows():
        if row["Datetime"] < ctime:
            continue
        open_time = row["Datetime"]
        cost = row["Close"]
        print(f"Purchased for {cost} at {open_time}")
        bound = (row["Current Vol"]/10000)*cost
        remainder = t2.loc[t2["index"] > row["index"]]
        for i, r in remainder.iterrows():
            if abs(r["Close"] - cost) >= bound*std_ct*(2*hurst):
                sale = r["Close"]
                ctime = r["Datetime"]
                print(f"Sold for {sale} at {ctime}")
                profit += (sale - cost)
                break
    return profit

In [ ]:
def t1_to_t2_backtest(ticker1, ticker2, correlated, std_ct):
    t1, t1_returns, t1_vol = conditional_vol(ticker1)
    t2, t2_returns, t2_vol = conditional_vol(ticker2)
    hurst = get_hurst_exponent(t2)
    if correlated:
        t1_diff = t1_returns - t1_vol
        t1_times = t1_diff[t1_diff > 0].reset_index()
    else:
        t1_diff = t1_returns + t1_vol
        t1_times = t1_diff[t1_diff < 0].reset_index()
    t2 = t2.reset_index().reset_index()
    t2_vol = t2_vol.reset_index()
    entries = t2.loc[t2["Datetime"].isin(t1_times["Datetime"])].reset_index(drop=True)
    entry_vols = t2_vol.loc[t2_vol["Datetime"].isin(t1_times["Datetime"])].reset_index(drop=True)
    entries["Current Vol"] = entry_vols["cond_vol"]
    ctime = entries["Datetime"][0]
    profit = 0
    for index, row in entries.iterrows():
        if row["Datetime"] < ctime:
            continue
        open_time = row["Datetime"]
        cost = row["Close"]
        print(f"Purchased for {cost} at {open_time}")
        bound = (row["Current Vol"]/10000)*cost
        remainder = t2.loc[t2["index"] > row["index"]]
        for i, r in remainder.iterrows():
            if abs(r["Close"] - cost) >= bound*std_ct*(2*hurst):
                sale = r["Close"]
                ctime = r["Datetime"]
                print(f"Sold for {sale} at {ctime}")
                profit += (sale - cost)
                break
    return profit

In [6]:
t1_to_t2_dynamic("SEDG", "ENPH", False, 1)

[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
Iteration:      1,   Func. Count:      8,   Neg. LLF: 33119.397808658934
Iteration:      2,   Func. Count:     17,   Neg. LLF: 32959.676493868436
Iteration:      3,   Func. Count:     26,   Neg. LLF: 32808.112696711265
Iteration:      4,   Func. Count:     35,   Neg. LLF: 32739.770693877526
Iteration:      5,   Func. Count:     44,   Neg. LLF: 32677.855182971212
Iteration:      6,   Func. Count:     53,   Neg. LLF: 32633.164373208176
Iteration:      7,   Func. Count:     62,   Neg. LLF: 32620.103478467547
Iteration:      8,   Func. Count:     71,   Neg. LLF: 32597.736089781025
Iteration:      9,   Func. Count:     80,   Neg. LLF: 32577.514052909144
Iteration:     10,   Func. Count:     89,   Neg. LLF: 32567.8575290

Iteration:     52,   Func. Count:    456,   Neg. LLF: 35654.887937688865
Iteration:     53,   Func. Count:    465,   Neg. LLF: 35639.4105450515
Iteration:     54,   Func. Count:    474,   Neg. LLF: 35623.85818391381
Iteration:     55,   Func. Count:    483,   Neg. LLF: 35606.91523878487
Iteration:     56,   Func. Count:    492,   Neg. LLF: 35591.167748665415
Iteration:     57,   Func. Count:    501,   Neg. LLF: 35583.28069479305
Iteration:     58,   Func. Count:    511,   Neg. LLF: 35577.174426058154
Iteration:     59,   Func. Count:    520,   Neg. LLF: 35567.95986894814
Iteration:     60,   Func. Count:    529,   Neg. LLF: 35561.44896493275
Iteration:     61,   Func. Count:    538,   Neg. LLF: 35554.10795317957
Iteration:     62,   Func. Count:    547,   Neg. LLF: 35544.98558727586
Iteration:     63,   Func. Count:    555,   Neg. LLF: 35534.78976669042
Iteration:     64,   Func. Count:    563,   Neg. LLF: 35514.47447054092
Iteration:     65,   Func. Count:    571,   Neg. LLF: 35504.95

Sold for 208.67999267578125 at 2022-04-07 10:44:00-04:00
Purchased for 208.67999267578125 at 2022-04-07 10:44:00-04:00
Sold for 209.52999877929688 at 2022-04-07 10:50:00-04:00
Purchased for 209.51499938964844 at 2022-04-07 11:06:00-04:00
Sold for 210.0 at 2022-04-07 11:08:00-04:00
Purchased for 209.61700439453125 at 2022-04-07 11:09:00-04:00
Sold for 208.8800048828125 at 2022-04-07 11:11:00-04:00
Purchased for 208.8800048828125 at 2022-04-07 11:11:00-04:00
Sold for 208.3000030517578 at 2022-04-07 11:13:00-04:00
Purchased for 207.14920043945312 at 2022-04-07 11:25:00-04:00
Sold for 206.86500549316406 at 2022-04-07 11:26:00-04:00
Purchased for 207.3000030517578 at 2022-04-07 11:31:00-04:00
Sold for 207.875 at 2022-04-07 11:32:00-04:00
Purchased for 207.36000061035156 at 2022-04-07 11:38:00-04:00
Sold for 207.00999450683594 at 2022-04-07 11:39:00-04:00
Purchased for 207.00999450683594 at 2022-04-07 11:39:00-04:00
Sold for 206.55499267578125 at 2022-04-07 11:43:00-04:00
Purchased for 205.0

Sold for 197.72999572753906 at 2022-04-08 13:38:00-04:00
Purchased for 197.58999633789062 at 2022-04-08 13:45:00-04:00
Sold for 197.1793975830078 at 2022-04-08 13:46:00-04:00
Purchased for 197.5800018310547 at 2022-04-08 14:00:00-04:00
Sold for 197.24000549316406 at 2022-04-08 14:02:00-04:00
Purchased for 197.09039306640625 at 2022-04-08 14:04:00-04:00
Sold for 196.89500427246094 at 2022-04-08 14:06:00-04:00
Purchased for 197.13800048828125 at 2022-04-08 14:12:00-04:00
Sold for 197.38999938964844 at 2022-04-08 14:13:00-04:00
Purchased for 197.1999969482422 at 2022-04-08 14:25:00-04:00
Sold for 196.9949951171875 at 2022-04-08 14:26:00-04:00
Purchased for 196.7050018310547 at 2022-04-08 14:27:00-04:00
Sold for 196.51499938964844 at 2022-04-08 14:32:00-04:00
Purchased for 196.51499938964844 at 2022-04-08 14:32:00-04:00
Sold for 196.29930114746094 at 2022-04-08 14:34:00-04:00
Purchased for 196.90499877929688 at 2022-04-08 14:56:00-04:00
Sold for 196.7205047607422 at 2022-04-08 14:57:00-04:

Sold for 187.75999450683594 at 2022-04-12 14:08:00-04:00
Purchased for 187.49000549316406 at 2022-04-12 14:12:00-04:00
Sold for 187.26499938964844 at 2022-04-12 14:13:00-04:00
Purchased for 187.26499938964844 at 2022-04-12 14:13:00-04:00
Sold for 186.9199981689453 at 2022-04-12 14:14:00-04:00
Purchased for 186.50999450683594 at 2022-04-12 14:29:00-04:00
Sold for 186.664306640625 at 2022-04-12 14:31:00-04:00
Purchased for 186.49000549316406 at 2022-04-12 14:33:00-04:00
Sold for 186.74000549316406 at 2022-04-12 14:34:00-04:00
Purchased for 186.6199951171875 at 2022-04-12 14:40:00-04:00
Sold for 186.3800048828125 at 2022-04-12 14:43:00-04:00
Purchased for 186.3800048828125 at 2022-04-12 14:43:00-04:00
Sold for 186.5500030517578 at 2022-04-12 14:44:00-04:00
Purchased for 187.39920043945312 at 2022-04-12 14:53:00-04:00
Sold for 187.05999755859375 at 2022-04-12 14:58:00-04:00
Purchased for 185.91000366210938 at 2022-04-12 15:03:00-04:00
Sold for 186.3699951171875 at 2022-04-12 15:06:00-04:00

...

Sold for 170.8300018310547 at 2022-04-27 10:46:00-04:00
Purchased for 169.02000427246094 at 2022-04-27 10:58:00-04:00
Sold for 169.75999450683594 at 2022-04-27 11:00:00-04:00
Purchased for 169.00999450683594 at 2022-04-27 11:03:00-04:00
Sold for 168.0 at 2022-04-27 11:04:00-04:00
Purchased for 166.72000122070312 at 2022-04-27 11:05:00-04:00
Sold for 166.27000427246094 at 2022-04-27 11:06:00-04:00
Purchased for 166.22000122070312 at 2022-04-27 11:09:00-04:00
Sold for 165.6300048828125 at 2022-04-27 11:10:00-04:00
Purchased for 164.07000732421875 at 2022-04-27 11:17:00-04:00
Sold for 164.9199981689453 at 2022-04-27 11:22:00-04:00
Purchased for 164.74000549316406 at 2022-04-27 11:23:00-04:00
Sold for 165.39500427246094 at 2022-04-27 11:25:00-04:00
Purchased for 164.11000061035156 at 2022-04-27 11:27:00-04:00
Sold for 163.26010131835938 at 2022-04-27 11:28:00-04:00
Purchased for 163.26010131835938 at 2022-04-27 11:28:00-04:00
Sold for 164.0800018310547 at 2022-04-27 11:30:00-04:00
Purchase

Sold for 164.44000244140625 at 2022-04-28 14:29:00-04:00
Purchased for 164.77999877929688 at 2022-04-28 14:31:00-04:00
Sold for 165.2100067138672 at 2022-04-28 14:33:00-04:00
Purchased for 166.0 at 2022-04-28 14:42:00-04:00
Sold for 166.1750030517578 at 2022-04-28 14:43:00-04:00
Purchased for 165.91000366210938 at 2022-04-28 14:54:00-04:00
Sold for 165.6699981689453 at 2022-04-28 14:55:00-04:00
Purchased for 165.6699981689453 at 2022-04-28 14:55:00-04:00
Sold for 166.3350067138672 at 2022-04-28 14:59:00-04:00
Purchased for 166.4282989501953 at 2022-04-28 15:28:00-04:00
Sold for 166.0399932861328 at 2022-04-28 15:29:00-04:00
Purchased for 166.0399932861328 at 2022-04-28 15:29:00-04:00
Sold for 165.73500061035156 at 2022-04-28 15:33:00-04:00
Purchased for 165.8000030517578 at 2022-04-28 15:38:00-04:00
Sold for 165.44000244140625 at 2022-04-28 15:43:00-04:00
Purchased for 164.64500427246094 at 2022-04-28 15:50:00-04:00
Sold for 164.88499450683594 at 2022-04-28 15:52:00-04:00
Purchased for

Sold for 162.1649932861328 at 2022-05-02 13:52:00-04:00
Purchased for 162.68800354003906 at 2022-05-02 14:00:00-04:00
Sold for 163.69000244140625 at 2022-05-02 14:02:00-04:00
Purchased for 163.53500366210938 at 2022-05-02 14:05:00-04:00
Sold for 163.875 at 2022-05-02 14:06:00-04:00
Purchased for 163.31500244140625 at 2022-05-02 14:09:00-04:00
Sold for 162.89999389648438 at 2022-05-02 14:11:00-04:00
Purchased for 162.5 at 2022-05-02 14:12:00-04:00
Sold for 162.19000244140625 at 2022-05-02 14:13:00-04:00
Purchased for 162.38999938964844 at 2022-05-02 14:25:00-04:00
Sold for 162.1699981689453 at 2022-05-02 14:26:00-04:00
Purchased for 163.12179565429688 at 2022-05-02 14:35:00-04:00
Sold for 163.44500732421875 at 2022-05-02 14:37:00-04:00
Purchased for 163.30999755859375 at 2022-05-02 14:39:00-04:00
Sold for 162.8699951171875 at 2022-05-02 14:41:00-04:00
Purchased for 164.64999389648438 at 2022-05-02 14:55:00-04:00
Sold for 164.33999633789062 at 2022-05-02 14:57:00-04:00
Purchased for 164.

Sold for 177.65499877929688 at 2022-05-04 09:52:00-04:00
Purchased for 176.50999450683594 at 2022-05-04 09:53:00-04:00
Sold for 176.02000427246094 at 2022-05-04 09:54:00-04:00
Purchased for 175.9600067138672 at 2022-05-04 09:59:00-04:00
Sold for 175.53570556640625 at 2022-05-04 10:00:00-04:00
Purchased for 176.57000732421875 at 2022-05-04 10:05:00-04:00
Sold for 176.16000366210938 at 2022-05-04 10:06:00-04:00
Purchased for 175.42999267578125 at 2022-05-04 10:15:00-04:00
Sold for 175.9600067138672 at 2022-05-04 10:20:00-04:00
Purchased for 175.8800048828125 at 2022-05-04 10:25:00-04:00
Sold for 176.4416046142578 at 2022-05-04 10:26:00-04:00
Purchased for 176.25 at 2022-05-04 10:34:00-04:00
Sold for 177.13999938964844 at 2022-05-04 10:35:00-04:00
Purchased for 177.69500732421875 at 2022-05-04 10:41:00-04:00
Sold for 178.17999267578125 at 2022-05-04 10:42:00-04:00
Purchased for 178.07220458984375 at 2022-05-04 10:51:00-04:00
Sold for 178.50759887695312 at 2022-05-04 10:54:00-04:00
Purchas

0.57928466796875

In [8]:
sedg = full_month("SEDG")
enph = full_month("ENPH")

[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed


In [36]:
merged = pd.merge(sedg, enph, how='inner', left_index=True, right_index=True)
merged = merged[["Close_x", "Close_y"]]
merged = merged.drop_duplicates()
merged
#merged.to_csv("SEDG-ENPH.csv", index=True)

Close_x     Close_y
Datetime                                         
2022-04-06 09:30:00-04:00  325.480011  208.000000
2022-04-06 09:31:00-04:00  326.464996  207.419998
2022-04-06 09:32:00-04:00  322.000000  207.259598
2022-04-06 09:33:00-04:00  321.160004  205.029999
2022-04-06 09:34:00-04:00  322.225006  205.009995
...                               ...         ...
2022-05-04 15:56:00-04:00  283.970001  191.990005
2022-05-04 15:57:00-04:00  284.200012  192.080002
2022-05-04 15:58:00-04:00  284.420013  192.035004
2022-05-04 15:59:00-04:00  284.600006  192.020004
2022-05-04 16:00:00-04:00  284.600006  191.940002

[7015 rows x 2 columns]

In [24]:
df = pd.DataFrame(list())
df.to_csv('filler.csv')

In [34]:
merged[-10:]

Close_x     Close_y
Datetime                                         
2022-05-04 16:00:00-04:00  284.600006  191.940002
2022-05-04 16:00:00-04:00  284.600006  191.940002
2022-05-04 16:00:00-04:00  284.600006  191.940002
2022-05-04 16:00:00-04:00  284.600006  191.940002
2022-05-04 16:00:00-04:00  284.600006  191.940002
2022-05-04 16:00:00-04:00  284.600006  191.940002
2022-05-04 16:00:00-04:00  284.600006  191.940002
2022-05-04 16:00:00-04:00  284.600006  191.940002
2022-05-04 16:00:00-04:00  284.600006  191.940002
2022-05-04 16:00:00-04:00  284.600006  191.940002

In [49]:
from backtest import backtest
import numpy as np
from scipy.optimize import minimize



'''
strat_function(preds, prices) - user specified mapping from past n days of price and analyst data to weights.
Returns: An array of asset weightings. The maximum weighting is 1, and the minimum is -1. The weights must sum to between -1 and 1. 

Refer to test datasets for the shape of input data. Both preds and prices will be 2 dimensional arrays, with number of columns equal to number of assets + 1.
Number of days equal to number of rows. The first column will be date data.

Your strategy function needs to work with this data to geenrate portfolio weights.


'''

def calc_conditional_vol(stock):
    
    
    
    return 



def strat_function(preds, prices): 
    # IGNORE PREDS FOR THIS    
    prices = np.array(prices)
    
    stock_1 = prices[:, 0]
    stock_2 = prices[:, 1]
    
    conditional_volatility = calc_conditional_vol(stock_1)
    
    
    
    
    
    
    buy_signal = True
    
    
    if buy_signal: 
        return [0, 1]
    if sell: 
        return [0, 0]

'''
Running the backtest - starting portfolio value of 10000, reading in data from these two locations.
'''
backtest(strat_function, 10000, "SEDG-ENPH.csv", "SEDG-ENPH.csv")



[325.4800109863281]
[325.4800109863281 326.4649963378906]
[325.4800109863281 326.4649963378906 322.0]
[325.4800109863281 326.4649963378906 322.0 321.1600036621094]
[325.4800109863281 326.4649963378906 322.0 321.1600036621094
 322.2250061035156]
[325.4800109863281 326.4649963378906 322.0 321.1600036621094
 322.2250061035156 321.3699951171875]
[325.4800109863281 326.4649963378906 322.0 321.1600036621094
 322.2250061035156 321.3699951171875 320.7699890136719]
[325.4800109863281 326.4649963378906 322.0 321.1600036621094
 322.2250061035156 321.3699951171875 320.7699890136719 319.989990234375]
[325.4800109863281 326.4649963378906 322.0 321.1600036621094
 322.2250061035156 321.3699951171875 320.7699890136719 319.989990234375
 321.00830078125]
[325.4800109863281 326.4649963378906 322.0 321.1600036621094
 322.2250061035156 321.3699951171875 320.7699890136719 319.989990234375
 321.00830078125 319.2174987792969]
[325.4800109863281 326.4649963378906 322.0 321.1600036621094
 322.2250061035156 321.3

[325.4800109863281 326.4649963378906 322.0 321.1600036621094
 322.2250061035156 321.3699951171875 320.7699890136719 319.989990234375
 321.00830078125 319.2174987792969 322.5779113769531 319.8800048828125
 319.84649658203125 320.4100036621094 319.9700012207031 320.3299865722656
 319.5400085449219 318.9800109863281 316.6683959960937 317.0950012207031
 317.8699951171875 318.94500732421875 320.4100036621094 320.2200012207031
 319.364990234375 318.8099975585937 319.7799987792969 318.0
 318.4599914550781 318.3399963378906 318.3550109863281 316.56500244140625
 316.760009765625 315.82000732421875 316.3550109863281 315.75
 315.9800109863281 316.94000244140625 316.0599975585937 316.5299987792969
 315.8900146484375 317.07000732421875 315.868408203125 316.5400085449219
 316.74371337890625 318.0 318.3900146484375 317.57000732421875
 317.8699951171875 318.7699890136719 318.3399963378906 318.70001220703125
 317.3900146484375 316.5899963378906 316.5150146484375 314.67999267578125
 314.8099975585937 31

 316.7499084472656 316.1199951171875 315.6199951171875]
[325.4800109863281 326.4649963378906 322.0 321.1600036621094
 322.2250061035156 321.3699951171875 320.7699890136719 319.989990234375
 321.00830078125 319.2174987792969 322.5779113769531 319.8800048828125
 319.84649658203125 320.4100036621094 319.9700012207031 320.3299865722656
 319.5400085449219 318.9800109863281 316.6683959960937 317.0950012207031
 317.8699951171875 318.94500732421875 320.4100036621094 320.2200012207031
 319.364990234375 318.8099975585937 319.7799987792969 318.0
 318.4599914550781 318.3399963378906 318.3550109863281 316.56500244140625
 316.760009765625 315.82000732421875 316.3550109863281 315.75
 315.9800109863281 316.94000244140625 316.0599975585937 316.5299987792969
 315.8900146484375 317.07000732421875 315.868408203125 316.5400085449219
 316.74371337890625 318.0 318.3900146484375 317.57000732421875
 317.8699951171875 318.7699890136719 318.3399963378906 318.70001220703125
 317.3900146484375 316.5899963378906 31

[325.4800109863281 326.4649963378906 322.0 321.1600036621094
 322.2250061035156 321.3699951171875 320.7699890136719 319.989990234375
 321.00830078125 319.2174987792969 322.5779113769531 319.8800048828125
 319.84649658203125 320.4100036621094 319.9700012207031 320.3299865722656
 319.5400085449219 318.9800109863281 316.6683959960937 317.0950012207031
 317.8699951171875 318.94500732421875 320.4100036621094 320.2200012207031
 319.364990234375 318.8099975585937 319.7799987792969 318.0
 318.4599914550781 318.3399963378906 318.3550109863281 316.56500244140625
 316.760009765625 315.82000732421875 316.3550109863281 315.75
 315.9800109863281 316.94000244140625 316.0599975585937 316.5299987792969
 315.8900146484375 317.07000732421875 315.868408203125 316.5400085449219
 316.74371337890625 318.0 318.3900146484375 317.57000732421875
 317.8699951171875 318.7699890136719 318.3399963378906 318.70001220703125
 317.3900146484375 316.5899963378906 316.5150146484375 314.67999267578125
 314.8099975585937 31

 319.760009765625]
[325.4800109863281 326.4649963378906 322.0 321.1600036621094
 322.2250061035156 321.3699951171875 320.7699890136719 319.989990234375
 321.00830078125 319.2174987792969 322.5779113769531 319.8800048828125
 319.84649658203125 320.4100036621094 319.9700012207031 320.3299865722656
 319.5400085449219 318.9800109863281 316.6683959960937 317.0950012207031
 317.8699951171875 318.94500732421875 320.4100036621094 320.2200012207031
 319.364990234375 318.8099975585937 319.7799987792969 318.0
 318.4599914550781 318.3399963378906 318.3550109863281 316.56500244140625
 316.760009765625 315.82000732421875 316.3550109863281 315.75
 315.9800109863281 316.94000244140625 316.0599975585937 316.5299987792969
 315.8900146484375 317.07000732421875 315.868408203125 316.5400085449219
 316.74371337890625 318.0 318.3900146484375 317.57000732421875
 317.8699951171875 318.7699890136719 318.3399963378906 318.70001220703125
 317.3900146484375 316.5899963378906 316.5150146484375 314.67999267578125
 3

...

 248.47999572753903 248.7400054931641]
[325.4800109863281 326.4649963378906 322.0 ... 248.47999572753903
 248.7400054931641 249.55999755859372]
[325.4800109863281 326.4649963378906 322.0 ... 248.7400054931641
 249.55999755859372 249.40499877929688]
[325.4800109863281 326.4649963378906 322.0 ... 249.55999755859372
 249.40499877929688 249.4900054931641]
[325.4800109863281 326.4649963378906 322.0 ... 249.40499877929688
 249.4900054931641 249.0200042724609]
[325.4800109863281 326.4649963378906 322.0 ... 249.4900054931641
 249.0200042724609 248.7749938964844]
[325.4800109863281 326.4649963378906 322.0 ... 249.0200042724609
 248.7749938964844 248.8800048828125]
[325.4800109863281 326.4649963378906 322.0 ... 248.7749938964844
 248.8800048828125 248.9600067138672]
[325.4800109863281 326.4649963378906 322.0 ... 248.8800048828125
 248.9600067138672 249.38999938964844]
[325.4800109863281 326.4649963378906 322.0 ... 248.9600067138672
 249.38999938964844 249.3000030517578]
[325.4800109863281 326.46

[325.4800109863281 326.4649963378906 322.0 ... 248.9250030517578
 248.9250030517578 248.9250030517578]
[325.4800109863281 326.4649963378906 322.0 ... 248.9250030517578
 248.9250030517578 250.0]
[325.4800109863281 326.4649963378906 322.0 ... 248.9250030517578 250.0
 250.0]
[325.4800109863281 326.4649963378906 322.0 ... 250.0 250.0 250.0]
[325.4800109863281 326.4649963378906 322.0 ... 250.0 250.0 250.0]
[325.4800109863281 326.4649963378906 322.0 ... 250.0 250.0
 249.8300018310547]
[325.4800109863281 326.4649963378906 322.0 ... 250.0 249.8300018310547
 249.8300018310547]
[325.4800109863281 326.4649963378906 322.0 ... 249.8300018310547
 249.8300018310547 249.8300018310547]
[325.4800109863281 326.4649963378906 322.0 ... 249.8300018310547
 249.8300018310547 249.8300018310547]
[325.4800109863281 326.4649963378906 322.0 ... 249.8300018310547
 249.8300018310547 250.51499938964844]
[325.4800109863281 326.4649963378906 322.0 ... 249.8300018310547
 250.51499938964844 250.51499938964844]
[325.48001

[325.4800109863281 326.4649963378906 322.0 ... 249.9900054931641
 249.9900054931641 249.9900054931641]
[325.4800109863281 326.4649963378906 322.0 ... 249.9900054931641
 249.9900054931641 249.9900054931641]
[325.4800109863281 326.4649963378906 322.0 ... 249.9900054931641
 249.9900054931641 250.0]
[325.4800109863281 326.4649963378906 322.0 ... 249.9900054931641 250.0
 250.0]
[325.4800109863281 326.4649963378906 322.0 ... 250.0 250.0 250.0]
[325.4800109863281 326.4649963378906 322.0 ... 250.0 250.0 250.0]
[325.4800109863281 326.4649963378906 322.0 ... 250.0 250.0
 249.1925048828125]
[325.4800109863281 326.4649963378906 322.0 ... 250.0 249.1925048828125
 249.1925048828125]
[325.4800109863281 326.4649963378906 322.0 ... 249.1925048828125
 249.1925048828125 249.1925048828125]
[325.4800109863281 326.4649963378906 322.0 ... 249.1925048828125
 249.1925048828125 249.1925048828125]
[325.4800109863281 326.4649963378906 322.0 ... 249.1925048828125
 249.1925048828125 249.30499267578125]
[325.4800109

[325.4800109863281 326.4649963378906 322.0 ... 247.25 247.25 247.25]
[325.4800109863281 326.4649963378906 322.0 ... 247.25 247.25 247.25]
[325.4800109863281 326.4649963378906 322.0 ... 247.25 247.25
 247.38499450683597]
[325.4800109863281 326.4649963378906 322.0 ... 247.25 247.38499450683597
 247.38499450683597]
[325.4800109863281 326.4649963378906 322.0 ... 247.38499450683597
 247.38499450683597 247.38499450683597]
[325.4800109863281 326.4649963378906 322.0 ... 247.38499450683597
 247.38499450683597 247.38499450683597]
[325.4800109863281 326.4649963378906 322.0 ... 247.38499450683597
 247.38499450683597 247.13999938964844]
[325.4800109863281 326.4649963378906 322.0 ... 247.38499450683597
 247.13999938964844 247.13999938964844]
[325.4800109863281 326.4649963378906 322.0 ... 247.13999938964844
 247.13999938964844 247.13999938964844]
[325.4800109863281 326.4649963378906 322.0 ... 247.13999938964844
 247.13999938964844 247.13999938964844]
[325.4800109863281 326.4649963378906 322.0 ... 247

KeyboardInterrupt: 